# Preprocess

In [369]:
pip install pulp


In [370]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics.pairwise import sigmoid_kernel
# Example data loading
data = pd.read_csv('/content/drive/MyDrive/CSV files/soccer-matches.csv')


In [371]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3690 entries, 0 to 3689
Data columns (total 50 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id_match            3690 non-null   int64  
 1   names               3690 non-null   object 
 2   home_away           3690 non-null   int64  
 3   managers            3679 non-null   object 
 4   formations          3690 non-null   object 
 5   attendance          3690 non-null   object 
 6   date                3690 non-null   object 
 7   stadium             3690 non-null   object 
 8   championship        3690 non-null   object 
 9   edition             2280 non-null   object 
 10  country             3690 non-null   object 
 11  score               3690 non-null   object 
 12  goals               3690 non-null   int64  
 13  goals_past          3690 non-null   int64  
 14  total_shots         3690 non-null   int64  
 15  woodwork            3690 non-null   int64  
 16  shots_

In [372]:
data[0:11]

id_match                 names  home_away  \
0          1                Cuiaba          0   
1          1             Juventude          1   
2          2   Red Bull Bragantino          1   
3          2        Chapecoense AF          0   
4          3            America MG          1   
5          3  Athletico Paranaense          0   
6          4             Santos FC          1   
7          4                 Bahia          0   
8          5            Fluminense          0   
9          5                Cuiaba          1   
10         6             Palmeiras          1   

                                managers formations attendance        date  \
0         Alberto Valentim do Carmo Neto      4-3-3          0  2021-05-29   
1   Marcos Vinícius dos Santos Gonçalves    4-2-3-1          0  2021-05-29   
2                      Mauricio Barbieri    4-2-3-1          0  2021-05-30   
3                          Felipe Endres    4-3-2-1          0  2021-05-30   
4      Luiz Carlos Cirne Lima de Lorenzi    4-1-4-1          0  2021-05-30   
5                 Paulo Autuori de Mello    4-2-3-1          0  2021-05-30   
6                   Fernando Diniz Silva      4-3-3          0  2021-05-30   
7         Luis Eduardo Barros Cavalcanti      4-3-3          0  2021-05-30   
8                  Roger Machado Marques    4-1-4-1          0  2021-06-06   
9                                    NaN    4-2-3-1          0  2021-06-06   
10                         Abel Ferreira      3-5-2          0  2021-05-30   

                             stadium           championship edition country  \
0                     Arena Pantanal  Campeonato Brasileiro     NaN  Brazil   
1                     Arena Pantanal  Campeonato Brasileiro     NaN  Brazil   
2                        Arena Condá  Campeonato Brasileiro     NaN  Brazil   
3                        Arena Condá  Campeonato Brasileiro     NaN  Brazil   
4                   Arena da Baixada  Campeonato Brasileiro     NaN  Brazil   
5                   Arena da Baixada  Campeonato Brasileiro     NaN  Brazil   
6   Estádio Roberto Santos (Pituaçu)  Campeonato Brasileiro     NaN  Brazil   
7   Estádio Roberto Santos (Pituaçu)  Campeonato Brasileiro     NaN  Brazil   
8                       São Januario  Campeonato Brasileiro     NaN  Brazil   
9                       São Januario  Campeonato Brasileiro     NaN  Brazil   
10               Estadio do Maracanã  Campeonato Brasileiro     NaN  Brazil   

    score  goals  goals_past  total_shots  woodwork  shots_on_target  \
0   2 - 2      2           2           14         0                2   
1   2 - 2      2           2            7         0                3   
2   0 - 3      3           0           18         2                8   
3   0 - 3      0           3           10         0                2   
4   1 - 0      0           1           14         0                4   
5   1 - 0      1           0           11         1                5   
6   3 - 0      0           3           12         0                4   
7   3 - 0      3           0            5         0                3   
8   1 - 0      1           0            8         0                3   
9   1 - 0      0           1           10         0                4   
10  1 - 0      0           1           12         0                5   

    shots_off_target  blocked_shots  total_possession  touches  total_passes  \
0                  8              4              59.4      682           490   
1                  3              1              40.6      518           342   
2                  8              2              56.1      750           552   
3                  6              2              43.9      620           428   
4                  6              4              43.5      602           429   
5                  5              1              56.5      715           557   
6                  5              3              65.7      756           563   
7                  2    

In [373]:
data.drop([ 'names', 'home_away', 'managers', 'attendance', 'date', 'stadium', 'championship', 'edition', 'country', 'woodwork', 'touches', 'was_dribbled', 'corner_accuracy', 'dispossessed', 'errors', 'fouls', 'offsides', 'start_minutes', 'end_minutes'], axis=1, inplace=True)

In [374]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3690 entries, 0 to 3689
Data columns (total 31 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id_match            3690 non-null   int64  
 1   formations          3690 non-null   object 
 2   score               3690 non-null   object 
 3   goals               3690 non-null   int64  
 4   goals_past          3690 non-null   int64  
 5   total_shots         3690 non-null   int64  
 6   shots_on_target     3690 non-null   int64  
 7   shots_off_target    3690 non-null   int64  
 8   blocked_shots       3690 non-null   int64  
 9   total_possession    3690 non-null   float64
 10  total_passes        3690 non-null   int64  
 11  accurate_passes     3690 non-null   int64  
 12  pass_success        3690 non-null   int64  
 13  key_passes          3690 non-null   int64  
 14  dribbles_attempted  3690 non-null   int64  
 15  dibles              3690 non-null   int64  
 16  dribbl

In [375]:
data[0:11]

id_match formations  score  goals  goals_past  total_shots  \
0          1      4-3-3  2 - 2      2           2           14   
1          1    4-2-3-1  2 - 2      2           2            7   
2          2    4-2-3-1  0 - 3      3           0           18   
3          2    4-3-2-1  0 - 3      0           3           10   
4          3    4-1-4-1  1 - 0      0           1           14   
5          3    4-2-3-1  1 - 0      1           0           11   
6          4      4-3-3  3 - 0      0           3           12   
7          4      4-3-3  3 - 0      3           0            5   
8          5    4-1-4-1  1 - 0      1           0            8   
9          5    4-2-3-1  1 - 0      0           1           10   
10         6      3-5-2  1 - 0      0           1           12   

    shots_on_target  shots_off_target  blocked_shots  total_possession  \
0                 2                 8              4              59.4   
1                 3                 3              1              40.6   
2                 8                 8              2              56.1   
3                 2                 6              2              43.9   
4                 4                 6              4              43.5   
5                 5                 5              1              56.5   
6                 4                 5              3              65.7   
7                 3                 2              0              34.3   
8                 3                 2              3              44.8   
9                 4                 5              1              55.2   
10                5                 6              1              38.2   

    total_passes  accurate_passes  pass_success  key_passes  \
0            490              417            85          13   
1            342              266            78           5   
2            552              483            88          15   
3            428              342            80           8   
4            429              351            82          10   
5            557              463            83           7   
6            563              501            89           9   
7            304              230            76           5   
8            394              333            85           6   
9            489              413            84           6   
10           300              244            81           6   

    dribbles_attempted  dibles  dribbles_past  dribbles_success  aerials_won  \
0                   21      12              8                57           21   
1                   11       8             12                73           23   
2                   20      14             11                70           16   
3                   15      11             14                73            4   
4                    6       4              7                67           13   
5                    8       7              4                88           24   
6                   17       8              9                47           12   
7                   16       9              8                56           10   
8                   16       9             14                56            7   
9                   22      14              9                64            9   
10                  13       5             12                38            4   

    aerial_success  offensive_aerials  defensive_aerials  tackles  \
0               48                 33                 11       19   
1               52                 11                 33       16   
2               80                 10                 10       12   
3               20                 10                 10       10   
4               35                 18                 19        7   
5               65                 19                 18        5   
6               55                 11                 11       12   
7               45                 11               

In [376]:
data_cleaned = data

In [377]:
unique_formations = data_cleaned['formations'].unique()
print(unique_formations)


['4-3-3' '4-2-3-1' '4-3-2-1' '4-1-4-1' '3-5-2' '3-4-1-2' '4-4-2' '4-4-1-1'
 '5-4-1' '3-4-3' '4-1-2-1-2' '3-1-4-2' '3-4-2-1' '4-5-1' '4-3-1-2'
 '4-2-2-2' '3-5-1-1' '4-1-3-2' '5-3-2' '3-3-3-1' '4-2-4-0' '3-4-3-d']


In [378]:
# Assuming your DataFrame is named 'data_cleaned'

# Define a dictionary mapping old values to new values
replacement_dict = {
    '3-4-3-d': '3-4-3',
    '4-2-4-0': '4-2-4'# Replace '4-4-2' with '4-3-3'
}

# Replace values in the 'formations' column
data_cleaned['formations'] = data_cleaned['formations'].replace(replacement_dict)

# Check the updated values
print(data_cleaned['formations'].unique())


['4-3-3' '4-2-3-1' '4-3-2-1' '4-1-4-1' '3-5-2' '3-4-1-2' '4-4-2' '4-4-1-1'
 '5-4-1' '3-4-3' '4-1-2-1-2' '3-1-4-2' '3-4-2-1' '4-5-1' '4-3-1-2'
 '4-2-2-2' '3-5-1-1' '4-1-3-2' '5-3-2' '3-3-3-1' '4-2-4']


In [379]:
data_cleaned.columns

Index(['id_match', 'formations', 'score', 'goals', 'goals_past', 'total_shots',
       'shots_on_target', 'shots_off_target', 'blocked_shots',
       'total_possession', 'total_passes', 'accurate_passes', 'pass_success',
       'key_passes', 'dribbles_attempted', 'dibles', 'dribbles_past',
       'dribbles_success', 'aerials_won', 'aerial_success',
       'offensive_aerials', 'defensive_aerials', 'tackles', 'tackle_success',
       'tackles_attempted', 'clearances', 'interceptions', 'corners', 'win',
       'draw', 'lose'],
      dtype='object')

In [380]:
data_cleaned.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3690 entries, 0 to 3689
Data columns (total 31 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id_match            3690 non-null   int64  
 1   formations          3690 non-null   object 
 2   score               3690 non-null   object 
 3   goals               3690 non-null   int64  
 4   goals_past          3690 non-null   int64  
 5   total_shots         3690 non-null   int64  
 6   shots_on_target     3690 non-null   int64  
 7   shots_off_target    3690 non-null   int64  
 8   blocked_shots       3690 non-null   int64  
 9   total_possession    3690 non-null   float64
 10  total_passes        3690 non-null   int64  
 11  accurate_passes     3690 non-null   int64  
 12  pass_success        3690 non-null   int64  
 13  key_passes          3690 non-null   int64  
 14  dribbles_attempted  3690 non-null   int64  
 15  dibles              3690 non-null   int64  
 16  dribbl

# First Model

In [381]:
import pandas as pd
from sklearn.metrics.pairwise import euclidean_distances
from IPython.display import display


teams = pd.read_csv('/content/drive/MyDrive/CSV files/teams_final_statistics (16).csv')
df = data_cleaned
if 'dibles' in df.columns:
    df['dribbles'] = df.pop('dibles')
else:
    df['dribbles'] = 0
# Step 1: Filter matches where your team lost
lost_games = df[df['lose'] == 1]



# Function to split the formation into defenders, midfielders, attackers, and additional positions (if any)
def split_formation(df):
    # Split the formation into parts
    formation_split = df['formations'].str.split('-')

    # Create columns based on the number of parts in the formation
    df['defenders'] = formation_split.str[0].astype(int)
    df['midfielders'] = formation_split.str[1].astype(int)

    # If there are 3 parts (e.g., 4-4-2), assign attackers to the third part
    df['attackers'] = formation_split.str[-1].astype(int)

    # If there are 4 parts (e.g., 4-2-3-1), assign the third part as 'advanced midfielders'
    df['advanced_midfielders'] = formation_split.apply(lambda x: int(x[2]) if len(x) > 3 else 0)

    return df


# Apply the split functions
# lost_games = split_score(lost_games)
lost_games = split_formation(lost_games)

# Step 2: Input row (split the score and formation in the same way)
input_row = teams.iloc[0].to_dict()


# Convert the input row to DataFrame
input_df = pd.DataFrame([input_row])

# Apply score and formation splitting to the input row
# input_df = split_score(input_df)
input_df = split_formation(input_df)

# Step 3: Define all relevant features to compare (excluding 'id_match', 'formation', 'score', 'win', 'draw', 'lose')
features_to_compare = [
    'goals', 'goals_past', 'total_shots', 'shots_on_target', 'shots_off_target',
    'blocked_shots', 'total_possession', 'total_passes', 'accurate_passes',
    'pass_success', 'key_passes', 'dribbles_attempted', 'dribbles',
    'dribbles_past', 'dribbles_success', 'aerials_won', 'aerial_success',
    'offensive_aerials', 'defensive_aerials', 'tackles', 'tackle_success',
    'tackles_attempted', 'clearances', 'interceptions', 'corners', 'defenders',
    'midfielders', 'attackers', 'advanced_midfielders'
]

# Step 4: Filter the lost games to keep only the relevant features
filtered_lost_games = lost_games[features_to_compare]

# Step 5: Calculate Euclidean distances between the input row and all lost games
distances = euclidean_distances(filtered_lost_games, input_df[features_to_compare])

# Step 6: Add distances to the filtered lost games DataFrame
lost_games['distance'] = distances

# Step 7: Sort by similarity (smallest distance first) and get top similar rows
top_n = 10  # Number of similar rows to return
similar_rows = lost_games.sort_values(by='distance')

# Step 8: Drop the distance column if no longer needed
similar_rows = similar_rows.drop(columns=['distance'])

# Output the most similar rows
# Step 8: Drop the distance column if no longer needed

# Output the most similar rows as a table
display(similar_rows)
rows = pd.DataFrame([input_row])

display(rows)
rows.to_csv('/content/sample_opponent_team.csv', index=False)


<ipython-input-381-711ed9b65e8d>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['defenders'] = formation_split.str[0].astype(int)
<ipython-input-381-711ed9b65e8d>:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['midfielders'] = formation_split.str[1].astype(int)
<ipython-input-381-711ed9b65e8d>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas

id_match formations  score  goals  goals_past  total_shots  \
1555       778      5-4-1  0 - 4      0           4            5   
809        405      5-4-1  5 - 0      0           5            1   
1425       713      4-3-3  2 - 0      0           2            9   
2345      1173      4-4-2  0 - 2      0           2            6   
1496       749      3-4-3  2 - 3      2           3           10   
950        476      5-3-2  0 - 3      0           3            6   
2971      1486      4-4-2  1 - 0      0           1            7   
1995       998      4-5-1  4 - 1      1           4            1   
558        281      4-5-1  1 - 0      0           1            2   
1327       664      5-4-1  1 - 0      0           1            7   
2587      1294    4-2-3-1  0 - 1      0           1            6   
1521       761      3-5-2  3 - 2      2           3           10   
1143       572      3-5-2  0 - 1      0           1            6   
1239       620      3-5-2  2 - 0      0           2            6   
3588      1795      4-4-2  1 - 0      0           1            4   
3474      1738    4-1-4-1  1 - 0      0           1           10   
2330      1166    4-1-4-1  2 - 3      2           3            7   
3171      1586      5-4-1  1 - 2      1           2           12   
3151      1576    4-4-1-1  1 - 0      0           1            7   
3084      1543    4-1-4-1  1 - 0      0           1            7   
3067      1534    3-4-1-2  4 - 0      0           4            5   
736        370      4-4-2  0 - 1      0           1           14   
2421      1211      4-4-2  4 - 1      1           4           10   
1054       528    4-1-4-1  1 - 3      1           3           11   
1516       759    4-3-2-1  3 - 2      2           3            4   
888        445    4-2-3-1  1 - 0      0           1            5   
2593      1297      5-3-2  3 - 2      2           3            7   
2500      1251      5-3-2  4 - 2      2           4           15   
3498      1750    4-1-4-1  1 - 0      0           1           13   
2217      1109    4-2-3-1  3 - 4      3           4            9   
2293      1147    4-2-3-1  3 - 0      0           3            4   
2036      1019    4-2-3-1  1 - 2      1           2            9   
3314      1658      4-4-2  8 - 1      1           8            8   
3003      1502      5-3-2  1 - 2      1           2            7   
1501       751      5-4-1  5 - 1      1           5            6   
2700      1351      4-4-2  3 - 1      1           3            6   
2819      1410    4-2-3-1  3 - 1      1           3            6   
989        495    4-4-1-1  3 - 0      0           3            4   
1422       712      4-3-3  5 - 1      1           5            5   
1377       689      4-5-1  0 - 2      0           2            3   
1161       581    4-2-3-1  1 - 2      1           2            7   
2487      1244      4-4-2  1 - 4      1           4           11   
130         66      5-4-1  2 - 1      1           2            9   
1469       735      4-3-3  1 - 0      0           1            6   
3322      1662    4-2-3-1  3 - 1      1           3           10   
1847       924      3-5-2  4 - 0      0           4            5   
918        460      5-4-1  0 - 5      0           5            6   
2452      1227    4-2-3-1  0 - 2      0           2            8   
1096       549      4-5-1  3 - 1      1           3            5   
2105      1053      4-3-3  1 - 0      0           1            3   
1178       590      4-4-2  0 - 1      0           1            6   
134         68      5-4-1  3 - 2      2           3            9   
2864      1433      4-4-2  3 - 2      2           3            5   
1023       512      4-4-2  1 - 4      1           4            8   
2612      1307      4-4-2  1 - 2      1           2           13   
1368       685    4-1-4-1  2 - 0      0           2            5   
2920      1461    4-2-3-1  0 - 1      0           1            9   
3382      1692      4-4-2  2 - 1      1           2           

Unnamed: 0  id_match formations      score  goals  goals_past  total_shots  \
0           0         1    4-3-2-1  0.0 - 0.0      0           0            4   

   shots_on_target  shots_off_target  blocked_shots  total_possession  \
0                1                 3              0         78.350515   

   total_passes  accurate_passes  pass_success  key_passes  \
0            76               55     72.368421           1   

   dribbles_attempted  dribbles  dribbles_past  dribbles_success  aerials_won  \
0                  10         0              0                 0            0   

   aerial_success  offensive_aerials  defensive_aerials  tackles  \
0               0                  0                  0        0   

   tackle_success  tackles_attempted  clearances  interceptions  corners  win  \
0               0                  0           1             19        0    0   

   draw  lose                             team_color  substitution_1  \
0     1     0  [     170.45      191.73       193.4]               0   

   substitution_2  substitution_3  substitution_4  substitution_5  
0               0               0               0               0

In [382]:
# Step 1: Get unique id_match values from lost games
lost_game_ids = similar_rows['id_match'].unique()

# Step 2: Filter the original DataFrame to get the rows of the winning team
winning_rows = df[(df['id_match'].isin(lost_game_ids)) & (df['win'] == 1)]

# Step 3: Exclude the losing team rows (if necessary, depending on your DataFrame structure)
# Assuming the winning team's rows are the only ones you want
# No need for further exclusion if you already filtered for 'win' == 1

# Display the winning rows as a table
display(winning_rows)


id_match formations  score  goals  goals_past  total_shots  \
2            2    4-2-3-1  0 - 3      3           0           18   
5            3    4-2-3-1  1 - 0      1           0           11   
7            4      4-3-3  3 - 0      3           0            5   
8            5    4-1-4-1  1 - 0      1           0            8   
11           6    4-2-3-1  1 - 0      1           0           14   
13           7    4-2-3-1  3 - 2      3           2           12   
16           9      3-5-2  1 - 2      2           1           18   
20          11    4-2-3-1  0 - 1      1           0            7   
23          12    3-4-1-2  5 - 1      5           1           14   
26          14      4-3-3  3 - 1      3           1           17   
28          15    4-2-3-1  2 - 0      2           0           20   
30          16    4-2-3-1  2 - 0      2           0            9   
33          17      4-4-2  0 - 3      3           0           11   
36          19    4-2-3-1  0 - 1      1           0           10   
39          20    4-1-4-1  0 - 1      1           0            6   
41          21    4-2-3-1  3 - 1      3           1           15   
47          24    4-2-3-1  1 - 2      2           1           21   
49          25      4-3-3  1 - 0      1           0            9   
51          26      5-4-1  0 - 1      1           0            9   
52          27    4-2-3-1  1 - 0      1           0            9   
59          30    4-1-4-1  0 - 1      1           0            6   
61          31      4-3-3  1 - 2      2           1            9   
62          32      5-4-1  1 - 0      1           0           10   
67          34      4-4-2  2 - 1      2           1           20   
73          37      4-3-3  0 - 1      1           0            6   
74          38    3-4-1-2  1 - 0      1           0           13   
77          39    4-1-4-1  0 - 3      3           0           13   
80          41    4-2-3-1  2 - 3      3           2            9   
83          42    4-1-4-1  2 - 1      2           1           15   
84          43    4-2-3-1  2 - 0      2           0           11   
90          46      4-4-2  2 - 1      2           1           19   
93          47    3-4-2-1  2 - 1      2           1           12   
102         52      4-3-3  2 - 1      2           1           16   
105         53    4-2-3-1  0 - 1      1           0            7   
107         54      4-4-2  1 - 0      1           0            8   
111         56    4-2-3-1  2 - 1      2           1           16   
116         59      4-3-3  2 - 0      2           0           11   
118         60    4-2-3-1  3 - 2      3           2           19   
122         62    4-2-3-1  1 - 0      1           0            9   
125         63    4-2-3-1  1 - 2      2           1           25   
126         64    4-2-3-1  3 - 1      3           1           12   
131         66      4-3-3  2 - 1      2           1           20   
135         68    3-4-1-2  3 - 2      3           2           22   
136         69    4-2-3-1  1 - 2      2           1           14   
138         70      4-3-3  4 - 1      4           1           19   
147         74    4-2-3-1  3 - 4      4           3           16   
149         75    4-2-3-1  1 - 4      4           1           11   
151         76    4-2-3-1  0 - 1      1           0           12   
152         77      4-3-3  1 - 0      1           0            8   
156         79    4-2-3-1  2 - 0      2           0           12   
158         80    4-2-3-1  0 - 1      1           0           10   
160         81    4-2-2-2  2 - 0      2           0            8   
163         82    4-2-3-1  1 - 2      2           1           12   
165         83    4-2-3-1  2 - 0      2           0           11   
166         84    4-2-3-1  0 - 1      1           0           14   
171         86    4-2-3-1  0 - 1      1           0           11   
173         87      4-4-2  0 - 2      2           0           12   
174         88    4-2-3-1  2 - 1      2           1           

In [383]:
import pandas as pd
from sklearn.metrics.pairwise import euclidean_distances
from IPython.display import display



# Step 1: Filter matches where your team lost
games = winning_rows

# Apply the split functions
games = split_formation(games)

# Step 2: Input row (split the score and formation in the same way)
input_row = teams.iloc[1].to_dict()

# Convert the input row to DataFrame
input_df = pd.DataFrame([input_row])

# Apply score and formation splitting to the input row
input_df = split_formation(input_df)

# Step 4: Filter the lost games to keep only the relevant features
filtered_games = games[features_to_compare]

# Step 5: Calculate Euclidean distances between the input row and all won games
distances = euclidean_distances(filtered_games, input_df[features_to_compare])

# Step 6: Add distances to the filtered lost games DataFrame
games['distance'] = distances

# Step 7: Sort by similarity (smallest distance first) and get top similar rows
top_n = 10  # Number of similar rows to return
similar_rows = games.sort_values(by='distance').head(top_n)

# Step 8: Drop the distance column if no longer needed
similar_rows = similar_rows.drop(columns=['distance'])
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
# Output the most similar rows
# Step 8: Drop the distance column if no longer needed

# Output the most similar rows as a table
display(similar_rows)
rows = pd.DataFrame([input_row])
display(rows)
rows.to_csv('/content/sample_my_team.csv', index=False)

<ipython-input-381-711ed9b65e8d>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['defenders'] = formation_split.str[0].astype(int)
<ipython-input-381-711ed9b65e8d>:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['midfielders'] = formation_split.str[1].astype(int)
<ipython-input-381-711ed9b65e8d>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas

id_match formations  score  goals  goals_past  total_shots  \
2422      1212    4-1-4-1  2 - 0      2           0            9   
2294      1148      4-4-2  1 - 0      1           0            4   
2960      1481    4-1-4-1  1 - 2      2           1            7   
1457       729      5-4-1  1 - 0      1           0            9   
3400      1701      4-4-2  1 - 0      1           0           10   
3680      1841    3-4-2-1  2 - 1      2           1           10   
3260      1631      4-3-3  1 - 4      4           1           17   
3440      1721      4-4-2  0 - 1      1           0            6   
1925       963      3-5-2  0 - 4      4           0           17   
1408       705      3-4-3  1 - 0      1           0            9   

      shots_on_target  shots_off_target  blocked_shots  total_possession  \
2422                3                 5              1              25.0   
2294                2                 2              0              26.4   
2960                3                 3              1              22.2   
1457                4                 4              1              21.7   
3400                4                 5              1              26.2   
3680                3                 6              1              25.5   
3260                7                 7              3              32.9   
3440                2                 4              0              22.8   
1925                8                 6              3              27.4   
1408                3                 1              5              24.3   

      total_passes  accurate_passes  pass_success  key_passes  \
2422           176              101            57           4   
2294           177              114            64           1   
2960           195               87            45           3   
1457           197              116            59           7   
3400           207              113            55           7   
3680           195              112            57           5   
3260           195              126            65          14   
3440           202              108            53           3   
1925           201              132            66          11   
1408           213              131            62           6   

      dribbles_attempted  dribbles_past  dribbles_success  aerials_won  \
2422                  18              5                28           13   
2294                  10             10                60           21   
2960                  12              8                58           23   
1457                  14             12                57           12   
3400                  16             14                19           13   
3680                  15             11                53           19   
3260                  11              7                55            9   
3440                   5             15                60            9   
1925                  16             10                31           11   
1408                  11             11                36           18   

      aerial_success  offensive_aerials  defensive_aerials  tackles  \
2422              37                 21                 14       19   
2294              72                 18                 11        7   
2960              47                 23                 26       20   
1457              50                 15                  9       13   
3400              42                 21                 10       18   
3680              42                 27                 18       27   
3260              38                 13                 11       18   
3440              25                 18                 18       28   
1925              42                 10                 16       21   
1408              47                 22                 16       14   

      tackle_success  tackles_attempted  clearances  interceptions  corners  \
2422              79        

Unnamed: 0  id_match formations      score  goals  goals_past  total_shots  \
0           1         1    3-5-1-1  0.0 - 0.0      0           0            1   

   shots_on_target  shots_off_target  blocked_shots  total_possession  \
0                1                 0              0         21.649485   

   total_passes  accurate_passes  pass_success  key_passes  \
0            21               12     57.142857           2   

   dribbles_attempted  dribbles  dribbles_past  dribbles_success  aerials_won  \
0                   0         0              0                 0            0   

   aerial_success  offensive_aerials  defensive_aerials  tackles  \
0               0                  0                  0        0   

   tackle_success  tackles_attempted  clearances  interceptions  corners  win  \
0               0                  0           1             11        0    0   

   draw  lose                             team_color  substitution_1  \
0     1     0  [     35.936      42.934      120.17]               0   

   substitution_2  substitution_3  substitution_4  substitution_5  
0               0               0               0               0

In [384]:
rows = similar_rows
display(rows)


id_match formations  score  goals  goals_past  total_shots  \
2422      1212    4-1-4-1  2 - 0      2           0            9   
2294      1148      4-4-2  1 - 0      1           0            4   
2960      1481    4-1-4-1  1 - 2      2           1            7   
1457       729      5-4-1  1 - 0      1           0            9   
3400      1701      4-4-2  1 - 0      1           0           10   
3680      1841    3-4-2-1  2 - 1      2           1           10   
3260      1631      4-3-3  1 - 4      4           1           17   
3440      1721      4-4-2  0 - 1      1           0            6   
1925       963      3-5-2  0 - 4      4           0           17   
1408       705      3-4-3  1 - 0      1           0            9   

      shots_on_target  shots_off_target  blocked_shots  total_possession  \
2422                3                 5              1              25.0   
2294                2                 2              0              26.4   
2960                3                 3              1              22.2   
1457                4                 4              1              21.7   
3400                4                 5              1              26.2   
3680                3                 6              1              25.5   
3260                7                 7              3              32.9   
3440                2                 4              0              22.8   
1925                8                 6              3              27.4   
1408                3                 1              5              24.3   

      total_passes  accurate_passes  pass_success  key_passes  \
2422           176              101            57           4   
2294           177              114            64           1   
2960           195               87            45           3   
1457           197              116            59           7   
3400           207              113            55           7   
3680           195              112            57           5   
3260           195              126            65          14   
3440           202              108            53           3   
1925           201              132            66          11   
1408           213              131            62           6   

      dribbles_attempted  dribbles_past  dribbles_success  aerials_won  \
2422                  18              5                28           13   
2294                  10             10                60           21   
2960                  12              8                58           23   
1457                  14             12                57           12   
3400                  16             14                19           13   
3680                  15             11                53           19   
3260                  11              7                55            9   
3440                   5             15                60            9   
1925                  16             10                31           11   
1408                  11             11                36           18   

      aerial_success  offensive_aerials  defensive_aerials  tackles  \
2422              37                 21                 14       19   
2294              72                 18                 11        7   
2960              47                 23                 26       20   
1457              50                 15                  9       13   
3400              42                 21                 10       18   
3680              42                 27                 18       27   
3260              38                 13                 11       18   
3440              25                 18                 18       28   
1925              42                 10                 16       21   
1408              47                 22                 16       14   

      tackle_success  tackles_attempted  clearances  interceptions  corners  \
2422              79        

In [385]:
rows.to_csv('/content/recommended_team_statistics.csv', index=False)

# Generating players data for testing

In [386]:
import pandas as pd
import random

# Regenerate data for soccer players with all modern football positions, including CDM, RW, LW
def generate_realistic_data():
    data = []

    # Extend positions to include all modern football roles
    positions = [
        'Goalkeeper', 'Right-back', 'Left-back', 'Center-back', 'Defensive Midfielder',
        'Central Midfielder', 'Attacking Midfielder', 'Right Winger',
        'Left Winger', 'Striker', 'Center Forward'
    ]

    for _ in range(1000):  # Generate for 1000 players
        position = random.choices(positions, weights=[1, 2, 2, 4, 2, 4, 3, 3, 3, 2, 2])[0]

        shirt_number = random.randint(1, 99)  # Assign random shirt numbers from 1 to 99
        minutes_per_game = random.randint(45, 90)

        if position in ['Striker', 'Center Forward']:
            goals = random.randint(5, 30)
            total_shots = random.randint(50, 100)
            shots_on_target = random.randint(20, 50)
            shots_off_target = total_shots - shots_on_target
            blocked_shots = random.randint(0, 10)
            saved_shots = 0
            total_passes = random.randint(100, 300)
            accurate_passes = random.randint(70, total_passes)
            pass_success = round((accurate_passes / total_passes) * 100, 2) if total_passes > 0 else 0
            key_passes = random.randint(20, 50)
            dribbles_attempted = random.randint(50, 100)
            dribbles = random.randint(30, dribbles_attempted)
            dribble_success = round((dribbles / dribbles_attempted) * 100, 2) if dribbles_attempted > 0 else 0
            dribbles_past = random.randint(10, 40)  # New feature: dribbles past opponents
            aerial_duels = random.randint(0, 10)
            aerial_success = random.uniform(40, 80)
            offensive_aerials_won = random.randint(5, 20)
            defensive_aerials_won = random.randint(0, 5)
            tackles_attempted = random.randint(5, 20)
            tackles_won = random.randint(3, tackles_attempted)
            tackle_success = round((tackles_won / tackles_attempted) * 100, 2) if tackles_attempted > 0 else 0
            clearances = random.randint(0, 10)
            interceptions = random.randint(0, 10)
            injuries = random.randint(0, 3)
            distance_covered = round(random.uniform(8, 12), 2)
            avg_speed = round(random.uniform(6, 8), 2)
            highest_speed = round(random.uniform(28, 35), 2)

        elif position in ['Central Midfielder', 'Attacking Midfielder']:
            goals = random.randint(3, 10)
            total_shots = random.randint(20, 60)
            shots_on_target = random.randint(10, 30)
            shots_off_target = total_shots - shots_on_target
            blocked_shots = random.randint(0, 10)
            saved_shots = 0
            total_passes = random.randint(500, 1000)
            accurate_passes = random.randint(400, total_passes)
            pass_success = round((accurate_passes / total_passes) * 100, 2) if total_passes > 0 else 0
            key_passes = random.randint(20, 40)
            dribbles_attempted = random.randint(20, 50)
            dribbles = random.randint(10, dribbles_attempted)
            dribble_success = round((dribbles / dribbles_attempted) * 100, 2) if dribbles_attempted > 0 else 0
            dribbles_past = random.randint(0, 10)  # New feature: dribbles past opponents
            aerial_duels = random.randint(5, 20)
            aerial_success = random.uniform(40, 70)
            offensive_aerials_won = random.randint(3, 10)
            defensive_aerials_won = random.randint(5, 10)
            tackles_attempted = random.randint(40, 80)
            tackles_won = random.randint(30, tackles_attempted)
            tackle_success = round((tackles_won / tackles_attempted) * 100, 2) if tackles_attempted > 0 else 0
            clearances = random.randint(5, 20)
            interceptions = random.randint(10, 30)
            injuries = random.randint(0, 3)
            distance_covered = round(random.uniform(9, 13), 2)
            avg_speed = round(random.uniform(5.5, 7.5), 2)
            highest_speed = round(random.uniform(25, 33), 2)

        elif position in ['Right-back', 'Left-back', 'Center-back']:
            goals = random.randint(0, 5)
            total_shots = random.randint(5, 20)
            shots_on_target = random.randint(0, 10)
            shots_off_target = total_shots - shots_on_target
            blocked_shots = random.randint(5, 20)
            saved_shots = 0
            total_passes = random.randint(300, 800)
            accurate_passes = random.randint(250, total_passes)
            pass_success = round((accurate_passes / total_passes) * 100, 2) if total_passes > 0 else 0
            key_passes = random.randint(5, 15)
            dribbles_attempted = random.randint(0, 20)
            dribbles = random.randint(0, dribbles_attempted)
            dribble_success = round((dribbles / dribbles_attempted) * 100, 2) if dribbles_attempted > 0 else 0
            dribbles_past = random.randint(0, 20)  # New feature: dribbles past opponents
            aerial_duels = random.randint(10, 30)
            aerial_success = random.uniform(50, 90)
            offensive_aerials_won = random.randint(0, 10)
            defensive_aerials_won = random.randint(10, 20)
            tackles_attempted = random.randint(50, 100)
            tackles_won = random.randint(40, tackles_attempted)
            tackle_success = round((tackles_won / tackles_attempted) * 100, 2) if tackles_attempted > 0 else 0
            clearances = random.randint(20, 50)
            interceptions = random.randint(20, 40)
            injuries = random.randint(0, 3)
            distance_covered = round(random.uniform(7, 11), 2)
            avg_speed = round(random.uniform(5, 7), 2)
            highest_speed = round(random.uniform(25, 30), 2)

        elif position == 'Defensive Midfielder':  # New: CDM
            goals = random.randint(1, 5)
            total_shots = random.randint(10, 40)
            shots_on_target = random.randint(5, 20)
            shots_off_target = total_shots - shots_on_target
            blocked_shots = random.randint(5, 20)
            saved_shots = 0
            total_passes = random.randint(400, 900)
            accurate_passes = random.randint(300, total_passes)
            pass_success = round((accurate_passes / total_passes) * 100, 2) if total_passes > 0 else 0
            key_passes = random.randint(10, 30)
            dribbles_attempted = random.randint(20, 50)
            dribbles = random.randint(10, dribbles_attempted)
            dribble_success = round((dribbles / dribbles_attempted) * 100, 2) if dribbles_attempted > 0 else 0
            dribbles_past = random.randint(0, 10)
            aerial_duels = random.randint(10, 30)
            aerial_success = random.uniform(60, 85)
            offensive_aerials_won = random.randint(5, 10)
            defensive_aerials_won = random.randint(10, 20)
            tackles_attempted = random.randint(60, 100)
            tackles_won = random.randint(50, tackles_attempted)
            tackle_success = round((tackles_won / tackles_attempted) * 100, 2) if tackles_attempted > 0 else 0
            clearances = random.randint(20, 40)
            interceptions = random.randint(20, 40)
            injuries = random.randint(0, 3)
            distance_covered = round(random.uniform(10, 13), 2)
            avg_speed = round(random.uniform(5, 7), 2)
            highest_speed = round(random.uniform(25, 30), 2)

        elif position in ['Right Winger', 'Left Winger']:  # New: RW and LW
            goals = random.randint(5, 15)
            total_shots = random.randint(30, 70)
            shots_on_target = random.randint(20, 50)
            shots_off_target = total_shots - shots_on_target
            blocked_shots = random.randint(0, 10)
            saved_shots = 0
            total_passes = random.randint(300, 700)
            accurate_passes = random.randint(250, total_passes)
            pass_success = round((accurate_passes / total_passes) * 100, 2) if total_passes > 0 else 0
            key_passes = random.randint(20, 50)
            dribbles_attempted = random.randint(50, 100)
            dribbles = random.randint(30, dribbles_attempted)
            dribble_success = round((dribbles / dribbles_attempted) * 100, 2) if dribbles_attempted > 0 else 0
            dribbles_past = random.randint(10, 40)
            aerial_duels = random.randint(10, 20)
            aerial_success = random.uniform(40, 70)
            offensive_aerials_won = random.randint(5, 15)
            defensive_aerials_won = random.randint(0, 5)
            tackles_attempted = random.randint(20, 40)
            tackles_won = random.randint(10, tackles_attempted)
            tackle_success = round((tackles_won / tackles_attempted) * 100, 2) if tackles_attempted > 0 else 0
            clearances = random.randint(0, 10)
            interceptions = random.randint(0, 10)
            injuries = random.randint(0, 3)
            distance_covered = round(random.uniform(9, 12), 2)
            avg_speed = round(random.uniform(6, 8), 2)
            highest_speed = round(random.uniform(28, 35), 2)

        else:  # Goalkeeper data
            goals = random.randint(0, 1)
            total_shots = 0
            shots_on_target = 0
            shots_off_target = 0
            blocked_shots = random.randint(50, 150)
            saved_shots = random.randint(50, 150)
            total_passes = random.randint(200, 500)
            accurate_passes = random.randint(150, total_passes)
            pass_success = round((accurate_passes / total_passes) * 100, 2) if total_passes > 0 else 0
            key_passes = random.randint(0, 10)
            dribbles_attempted = 0
            dribbles = 0
            dribble_success = 0
            dribbles_past = 0
            aerial_duels = random.randint(0, 10)
            aerial_success = random.uniform(50, 90)
            offensive_aerials_won = 0
            defensive_aerials_won = random.randint(0, 5)
            tackles_attempted = random.randint(0, 10)
            tackles_won = random.randint(0, tackles_attempted)
            tackle_success = round((tackles_won / tackles_attempted) * 100, 2) if tackles_attempted > 0 else 0
            clearances = random.randint(0, 10)
            interceptions = random.randint(0, 10)
            injuries = random.randint(0, 3)
            distance_covered = round(random.uniform(3, 6), 2)
            avg_speed = round(random.uniform(4, 6), 2)
            highest_speed = round(random.uniform(20, 25), 2)

        data.append([
            position, shirt_number, goals, total_shots, shots_on_target,
            shots_off_target, blocked_shots, saved_shots, total_passes, accurate_passes, pass_success, key_passes,
            dribbles_attempted, dribbles, dribble_success, dribbles_past, aerial_duels, aerial_success,
            offensive_aerials_won, defensive_aerials_won, tackles_attempted, tackles_won, tackle_success,
            clearances, interceptions, injuries, distance_covered, avg_speed, highest_speed
        ])

    columns = [
        'Position', 'Shirt_number', 'Goals', 'Total_shots',
        'Shots_on_Target', 'Shots_off_Target', 'Blocked_shots', 'Saved_shots', 'Total_passes', 'Accurate_passes',
        'Pass_success', 'Key_passes', 'Dribbles_attempted', 'Dribbles', 'Dribbles_success', 'Dribbles_past',
        'Aerial_duels', 'Aerial_success', 'Offensive_aerials', 'Defensive_aerials', 'Tackles_attempted',
        'Tackles_won', 'Tackle_success', 'Clearances', 'Interceptions', 'Injuries', 'Distance_covered',
        'Avg_speed', 'Highest_speed'
    ]

    df = pd.DataFrame(data, columns=columns)

    df.to_csv('/content/generated_player_data_modern_positions.csv', index=False)
    return df

df = generate_realistic_data()


In [387]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 29 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Position            1000 non-null   object 
 1   Shirt_number        1000 non-null   int64  
 2   Goals               1000 non-null   int64  
 3   Total_shots         1000 non-null   int64  
 4   Shots_on_Target     1000 non-null   int64  
 5   Shots_off_Target    1000 non-null   int64  
 6   Blocked_shots       1000 non-null   int64  
 7   Saved_shots         1000 non-null   int64  
 8   Total_passes        1000 non-null   int64  
 9   Accurate_passes     1000 non-null   int64  
 10  Pass_success        1000 non-null   float64
 11  Key_passes          1000 non-null   int64  
 12  Dribbles_attempted  1000 non-null   int64  
 13  Dribbles            1000 non-null   int64  
 14  Dribbles_success    1000 non-null   float64
 15  Dribbles_past       1000 non-null   int64  
 16  Aerial_

# Second Model

In [388]:
from pulp import LpProblem, LpVariable, lpSum, LpMaximize, LpStatus
from collections import Counter
import numpy as np

def split_formation(formation):
    return list(map(int, formation.split('-')))


# Get the list of features that should be maximized but are missing from the input row

def count_players_per_position(formation):
    """
    Given a formation string (e.g., '4-4-2' or '4-3-2-1'), this function returns a count of players
    assigned to each position group (defender, midfielder, forward).
    """
    # Parse the formation string into a list of integers
    formation_numbers = list(map(int, formation.split('-')))

    # Define the standard position groups for each section
    position_groups = {
        'defender': ['Right-back', 'Left-back', 'Center-back'],
        'midfielder': ['Defensive Midfielder', 'Central Midfielder', 'Attacking Midfielder', 'Right Winger', 'Left Winger'],
        'forward': ['Striker', 'Center Forward']
    }

    # Create a counter for all positions
    position_counter = Counter()

    # Number of defenders, midfielders, and forwards in the formation
    num_defenders = formation_numbers[0]
    num_midfielders = formation_numbers[1] if len(formation_numbers) > 1 else 0
    num_midfielders_advanced = formation_numbers[2] if len(formation_numbers) > 3 else 0
    num_forwards = formation_numbers[-1]

    # Assign defenders
    if num_defenders == 4:
        position_counter['Center-back'] = 2
        position_counter['Right-back'] = 1
        position_counter['Left-back'] = 1
    elif num_defenders == 3:
        position_counter['Center-back'] = 3
    elif num_defenders == 5:
        position_counter['Center-back'] = 3
        position_counter['Right-back'] = 1
        position_counter['Left-back'] = 1

    # Assign midfielders
    if num_midfielders == 4:
        position_counter['Central Midfielder'] = 2
        position_counter['Right Winger'] = 1
        position_counter['Left Winger'] = 1
    elif num_midfielders == 3:
        position_counter['Central Midfielder'] = 2
        position_counter['Attacking Midfielder'] = 1
    elif num_midfielders == 5:
        position_counter['Central Midfielder'] = 3
        position_counter['Right Winger'] = 1
        position_counter['Left Winger'] = 1

    # Assign advanced midfielders if any (for 4-digit formations)
    if num_midfielders_advanced > 0:
        position_counter['Attacking Midfielder'] += num_midfielders_advanced

    # Assign forwards
    if num_forwards == 2:
        position_counter['Striker'] = 1
        position_counter['Center Forward'] = 1
    elif num_forwards == 1:
        position_counter['Striker'] = 1
    elif num_forwards >= 3:
        position_counter['Striker'] = 2
        position_counter['Center Forward'] = 1

    return position_counter

# Stats to maximize based on new positions

STATS_TO_MAXIMIZE = {
    'Goalkeeper': ['aerial_success', 'blocked_shots'],
    'Right-back': ['tackles_attempted', 'tackle_success', 'clearances', 'interceptions', 'dribbles_success', 'aerial_success', 'pass_success'],
    'Left-back': ['tackles_attempted', 'tackle_success', 'clearances', 'interceptions', 'dribbles_success', 'aerial_success', 'pass_success'],
    'Center-back': ['tackles_attempted', 'tackle_success', 'clearances', 'interceptions', 'aerial_success', 'pass_success', 'defensive_aerials'],
    'Defensive Midfielder': ['tackles_attempted', 'interceptions', 'pass_success', 'key_passes', 'defensive_aerials'],
    'Central Midfielder': ['total_passes', 'accurate_passes', 'key_passes', 'dribbles_attempted', 'dribbles_success', 'pass_success', 'dribbles'],
    'Attacking Midfielder': ['goals', 'key_passes', 'dribbles_attempted', 'dribbles_success', 'pass_success', 'shots_on_target', 'dribbles', 'offensive_aerials'],
    'Right Winger': ['goals', 'assists', 'key_passes', 'dribbles_attempted', 'dribbles_success', 'crossing_accuracy', 'shots_on_target', 'pass_success', 'dribbles'],
    'Left Winger': ['goals', 'assists', 'key_passes', 'dribbles_attempted', 'dribbles_success', 'crossing_accuracy', 'shots_on_target', 'pass_success', 'dribbles'],
    'Striker': ['goals', 'shots_on_target', 'total_shots', 'key_passes', 'aerial_success', 'dribbles_success', 'pass_success', 'offensive_aerials'],
    'Center Forward': ['goals', 'shots_on_target', 'total_shots', 'key_passes', 'aerial_success', 'dribbles_success', 'pass_success', 'offensive_aerials']
}

# Stats to minimize based on new positions (without features after 'defensive aerials')
STATS_TO_MINIMIZE = {
    'Goalkeeper': ['goals_past', 'dribbles_past'],
    'Right-back': ['dribbles_past', 'injuries'],
    'Left-back': ['dribbles_past', 'injuries'],
    'Center-back': ['dribbles_past'],
    'Defensive Midfielder': ['dribbles_past', 'injuries'],
    'Central Midfielder': ['injuries'],
    'Attacking Midfielder': ['shots_off_target'],
    'Right Winger': ['shots_off_target', 'injuries'],
    'Left Winger': ['shots_off_target', 'injuries'],
    'Striker': ['shots_off_target', 'injuries'],
    'Center Forward': ['shots_off_target', 'injuries']
}

# Absent features to maximize based on new positions (features after 'defensive aerials' and not in stats to maximize/minimize)
ABSENT_FEATURES_TO_MAXIMIZE = {
    'Goalkeeper': ['saved_shots', 'avg_speed', 'highest_speed', 'aerial_duels'],
    'Right-back': ['distance_covered', 'avg_speed', 'highest_speed', 'tackles_won'],
    'Left-back': ['distance_covered', 'avg_speed', 'highest_speed', 'tackles_won'],
    'Center-back': ['distance_covered', 'avg_speed', 'highest_speed', 'tackles_won'],
    'Defensive Midfielder': ['distance_covered', 'aerial_duels', 'tackles_won'],
    'Central Midfielder': ['distance_covered', 'aerial_duels'],
    'Attacking Midfielder': ['highest_speed'],
    'Right Winger': ['highest_speed', 'distance_covered'],
    'Left Winger': ['highest_speed', 'distance_covered'],
    'Striker': ['aerial_duels'],
    'Center Forward': ['aerial_duels']
}





# Feature index map for player_stats and target_stats
FEATURE_INDEX_MAP = {
    'goals': 0,
    'total_shots': 1,
    'shots_on_target': 2,
    'shots_off_target': 3,
    'blocked_shots': 4,
    'total_passes': 5,
    'accurate_passes': 6,
    'pass_success': 7,
    'key_passes': 8,
    'dribbles_attempted': 9,
    'dribbles': 10,
    'dribbles_success': 11,
    'dribbles_past': 12,
    'aerial_success': 13,
    'tackles_attempted': 14,
    'tackle_success': 15,
    'clearances': 16,
    'interceptions': 17,
    'offensive_aerials': 18,
    'defensive_aerials': 19,
    'distance_covered': 20,
    'avg_speed': 21,
    'highest_speed': 22,
    'saved_shots': 23,
    'aerial_duels': 24,
    'tackles_won': 25
}


# Get indices of features to maximize and minimize
def get_relevant_feature_indices(position):
    max_features = [FEATURE_INDEX_MAP[feat] for feat in STATS_TO_MAXIMIZE[position] if feat in FEATURE_INDEX_MAP]
    min_features = [FEATURE_INDEX_MAP[feat] for feat in STATS_TO_MINIMIZE[position] if feat in FEATURE_INDEX_MAP] # Check if the feature exists in FEATURE_INDEX_MAP
    # print(f"Position: {position}")
    # print(f"Max features: {max_features}")
    # print(f"Min features: {min_features}")
    return max_features, min_features

# Modified objective function to maximize and minimize based on position
def objective(player_vars, player_stats, target_stats, max_features, min_features, absent_features):
    team_max_stats = [lpSum(player_vars[i] * player_stats[i][j] for i in range(len(player_vars))) for j in max_features]
    team_min_stats = [lpSum(player_vars[i] * player_stats[i][j] for i in range(len(player_vars))) for j in min_features]
    absent_stats = [lpSum(player_vars[i] * player_stats[i][j] for i in range(len(player_vars))) for j in absent_features]

    # Maximize the sum of relevant features to maximize
    maximize_term = lpSum(lpSum(team_max_stats[j] - target_stats[max_features[j]] for j in range(len(max_features))))
    maximize_absent_term = lpSum(absent_stats)
    # Minimize the sum of relevant features to minimize
    minimize_term = lpSum(lpSum(target_stats[min_features[j]] - team_min_stats[j] for j in range(len(min_features))))

    # The final objective is to maximize the difference for max features and minimize the difference for min features
    return maximize_term + maximize_absent_term - minimize_term

# Function to recommend players based on the input_row and the player data
def recommend_team(input_row, player_data):
    formation = input_row['formations']
    position_counts = count_players_per_position(formation)

    # Required players based on formation
    num_goalkeepers = 1
    num_right_backs = position_counts['Right-back']
    num_left_backs = position_counts['Left-back']
    num_center_backs = position_counts['Center-back']
    num_defensive_midfielders = position_counts['Defensive Midfielder']
    num_central_midfielders = position_counts['Central Midfielder']
    num_attacking_midfielders = position_counts['Attacking Midfielder']
    num_right_wingers = position_counts['Right Winger']
    num_left_wingers = position_counts['Left Winger']
    num_strikers = position_counts['Striker']
    num_center_forwards = position_counts['Center Forward']
    player_data.columns = player_data.columns.str.lower()

    # Separate player data based on positions
    goalkeepers = player_data[player_data['position'].str.contains('Goalkeeper')].index

# Instead of aggregating, we'll get individual defenders
    right_backs = player_data[player_data['position'].str.contains('Right-back')].index
    left_backs = player_data[player_data['position'].str.contains('Left-back')].index
    center_backs = player_data[player_data['position'].str.contains('Center-back')].index
    defensive_midfielders = player_data[player_data['position'].str.contains('Defensive Midfielder')].index
    central_midfielders = player_data[player_data['position'].str.contains('Central Midfielder')].index
    attacking_midfielders = player_data[player_data['position'].str.contains('Attacking Midfielder')].index
    right_wingers = player_data[player_data['position'].str.contains('Right Winger')].index
    left_wingers = player_data[player_data['position'].str.contains('Left Winger')].index
    strikers = player_data[player_data['position'].str.contains('Striker')].index
    center_forwards = player_data[player_data['position'].str.contains('Center Forward')].index

    # Prepare the player stats and constraints
    player_stats = player_data[['goals', 'total_shots', 'shots_on_target', 'shots_off_target', 'blocked_shots',
                                'total_passes', 'accurate_passes', 'pass_success', 'key_passes', 'dribbles_attempted',
                                'dribbles', 'dribbles_success', 'dribbles_past', 'aerial_success',
                                'tackles_attempted', 'tackles_success', 'clearances', 'interceptions', 'offensive_aerials', 'defensive_aerials',
                                'injuries', 'distance_covered', 'avg_speed', 'highest_speed', 'saved_shots', 'aerial_duels',
                                'tackles_won']].values

    target_stats = np.array([input_row['goals'], input_row['total_shots'], input_row['shots_on_target'],
                             input_row['shots_off_target'], input_row['blocked_shots'], input_row['total_passes'],
                             input_row['accurate_passes'], input_row['pass_success'], input_row['key_passes'], input_row['dribbles_attempted'],
                             input_row['dribbles'], input_row['dribbles_success'], input_row['dribbles_past'],
                             input_row['aerial_success'], input_row['tackles_attempted'], input_row['tackles_success'],
                             input_row['clearances'], input_row['interceptions'], input_row['goals_past'],
                             input_row['aerials_won'], input_row['offensive_aerials'], input_row['defensive_aerials'],
                             input_row['tackles']])

    # Get absent features


    # Create a linear programming problem
    problem = LpProblem("Team_Selection", LpMaximize)

    # Create integer decision variables for each player
    player_vars = [LpVariable(f'player_{i}', lowBound=0, cat='Binary') for i in range(len(player_data))]

    # Define constraints based on the number of players per position
    problem += lpSum([player_vars[i] for i in goalkeepers]) == num_goalkeepers, "Goalkeeper_Constraint"
    problem += lpSum([player_vars[i] for i in right_backs]) == num_right_backs, "Right_Back_Constraint"
    problem += lpSum([player_vars[i] for i in left_backs]) == num_left_backs, "Left_Back_Constraint"
    problem += lpSum([player_vars[i] for i in center_backs]) == num_center_backs, "Center_Back_Constraint"
    problem += lpSum([player_vars[i] for i in defensive_midfielders]) == num_defensive_midfielders, "Defensive_Midfielder_Constraint"
    problem += lpSum([player_vars[i] for i in central_midfielders]) == num_central_midfielders, "Central_Midfielder_Constraint"
    problem += lpSum([player_vars[i] for i in attacking_midfielders]) == num_attacking_midfielders, "Attacking_Midfielder_Constraint"
    problem += lpSum([player_vars[i] for i in right_wingers]) == num_right_wingers, "Right_Winger_Constraint"
    problem += lpSum([player_vars[i] for i in left_wingers]) == num_left_wingers, "Left_Winger_Constraint"
    problem += lpSum([player_vars[i] for i in strikers]) == num_strikers, "Striker_Constraint"
    problem += lpSum([player_vars[i] for i in center_forwards]) == num_center_forwards, "Center_Forward_Constraint"

    # Injury constraint
    injury_limit = 3
    for i in range(len(player_vars)):
        problem += player_vars[i] * player_data['injuries'].iloc[i] <= injury_limit, f'Injury_Constraint_{i}'

    # Set the objective for each position
    positions = {
    'Goalkeeper': goalkeepers,
    'Right-back': right_backs,
    'Left-back': left_backs,
    'Center-back': center_backs,
    'Defensive Midfielder': defensive_midfielders,
    'Central Midfielder': central_midfielders,
    'Attacking Midfielder': attacking_midfielders,
    'Right Winger': right_wingers,
    'Left Winger': left_wingers,
    'Striker': strikers,
    'Center Forward': center_forwards
    }


    # Define the objective based on the position
    for position, indices in positions.items():
        max_features, min_features = get_relevant_feature_indices(position)
        absent_features = [FEATURE_INDEX_MAP[feat] for feat in ABSENT_FEATURES_TO_MAXIMIZE[position] if feat in FEATURE_INDEX_MAP]

        if len(indices) > 0:
            problem += objective(player_vars, player_stats, target_stats, max_features, min_features, absent_features)

    # Solve the problem
    problem.solve()

    # Check if the optimization was successful
    if LpStatus[problem.status] == 'Optimal':
        # Continue from where we handle the optimization result
        # Extract the selected players based on the optimization result
        selected_players = player_data[[player_vars[i].varValue > 0 for i in range(len(player_data))]]

        # Calculate the selected team's stats
        team_stats = selected_players[['goals', 'total_shots', 'shots_on_target', 'shots_off_target', 'blocked_shots', 'saved_shots',
                                       'total_passes', 'accurate_passes', 'pass_success', 'key_passes', 'dribbles_attempted', 'dribbles',
                                       'dribbles_success', 'aerial_duels', 'aerial_success', 'offensive_aerials', 'defensive_aerials',
                                       'tackles_attempted', 'tackles_won', 'tackle_success', 'clearances', 'interceptions', 'injuries',
                                       'distance_covered', 'avg_speed', 'highest_speed']].sum()

        # Print or return the selected players and team stats


        return selected_players, team_stats

    else:
        print("No optimal solution found.")
        return None, None

# Example usage

match_data = rows

input_row = match_data.iloc[0].to_dict()
row = pd.DataFrame([input_row])
 #  comment this line for the new data

# Assuming 'player_data' is a DataFrame containing the player stats
player_data = pd.read_csv('/content/drive/MyDrive/CSV files/team_1_player_statistics (16).csv')

#uncomment those lines for the new data
player_data['shirt_number'] = player_data.pop('shirtNumber')
player_data['pass_success'] = player_data.pop('%_pass_success')
player_data['dribbles_success'] = player_data.pop('%_dribbles_success')
player_data['aerial_success'] = player_data.pop('%_aerial_success')
player_data['tackles_success'] = player_data.pop('%_tackles_success')

input_row['tackles_success'] = input_row.pop('tackle_success')


selected_players, team_stats = recommend_team(input_row, player_data)

# Output the recommended team and their collective stats
if selected_players is not None:
    print("\nRecommended Team:")
    display(selected_players)
    selected_players.to_csv('/content/selected_players.csv', index=False)
    print("\nTeam Stats:")
    display(team_stats)
    display(input_row)


No optimal solution found.


/usr/local/lib/python3.10/dist-packages/pulp/pulp.py:1650: UserWarning: Overwriting previously set objective.
  warnings.warn("Overwriting previously set objective.")


# code to correct the shirt number that need to be merged with the second model

In [389]:
import pandas as pd
from collections import Counter
import difflib  # For finding similar numbers

class PlayerStats:
    def __init__(self, input_df, correct_shirt_numbers):
        # Initialize the input DataFrame
        self.input_df = input_df
        self.correct_shirt_numbers = correct_shirt_numbers  # List of correct shirt numbers

        # Define the desired column structure for the final output (for reference only)
        self.columns = [
        'position', 'shirt_number', 'goals', 'total_shots',
        'shots_on_target', 'shots_off_target', 'blocked_shots', 'saved_shots', 'total_passes', 'accurate_passes',
        'pass_success', 'key_passes', 'dribbles_attempted', 'dribbles', 'dribbles_success', 'dribbles_past',
        'aerial_duels', 'aerial_success', 'offensive_aerials', 'defensive_aerials', 'tackles_attempted',
        'tackles_won', 'tackle_success', 'clearances', 'interceptions', 'injuries', 'distance_covered',
        'avg_speed', 'highest_speed'
    ]

    def correct_shirt_numbers_func(self):
        """
        Correct incorrect shirt numbers by finding the closest match from the correct list.
        """
        def find_closest_shirt_number(incorrect_number):
            # Find the closest matching correct shirt number
            correct_number = difflib.get_close_matches(str(incorrect_number), self.correct_shirt_numbers, n=1, cutoff=0.6)
            return correct_number[0] if correct_number else incorrect_number

        # Apply the correction
        self.input_df['corrected_shirt_number'] = self.input_df['shirt_number'].apply(find_closest_shirt_number)

    def process_data(self):
        # Step 1: Correct the shirt numbers before merging
        self.correct_shirt_numbers_func()

        # Step 2: Combine rows based on corrected 'shirt_number' and 'team' by summing all columns
        grouped = self.input_df.groupby(['corrected_shirt_number']).agg({
            'position': 'first',  # Assuming 'Position' does not change for the same 'shirt_number'
            'goals': 'sum',
            'total_shots': 'sum',
            'shots_on_target': 'sum',
            'shots_off_target': 'sum',
            'blocked_shots': 'sum',
            'saved_shots': 'sum',
            'total_passes': 'sum',
            'accurate_passes': 'sum',
            'pass_success': lambda x: x[x != 0].mean() if (x != 0).any() else 0,
            'key_passes': 'sum',
            'dribbles_attempted': 'sum',
            'dribbles': 'sum',
            'dribbles_success': lambda x: x[x != 0].mean() if (x != 0).any() else 0,
            'dribbles_past': 'sum',
            'aerial_duels': 'sum',
            'aerial_success': lambda x: x[x != 0].mean() if (x != 0).any() else 0,
            'offensive_aerials': 'sum',
            'defensive_aerials': 'sum',
            'tackles_attempted': 'sum',
            'tackles_won': 'sum',
            'tackles_success': lambda x: x[x != 0].mean() if (x != 0).any() else 0,
            'clearances': 'sum',
            'interceptions': 'sum',
            'injuries': 'sum',
            'distance_covered': 'sum',
            'avg_speed': lambda x: x[x != 0].mean() if (x != 0).any() else 0,  # Mean of non-zero values or 0
            'highest_speed': 'max',  # Max of highest_speed
        }).reset_index()

        # Step 3: Assign the team_color column manually


        print(f"grouped length :{len(grouped)}")

        return grouped



In [390]:
correct_shirt_numbers = ['11', '19', '12', '45']
player_stats = PlayerStats(player_data, correct_shirt_numbers)

# Process the data to merge by corrected shirt numbers
processed_data = player_stats.process_data()

# Output the processed data
print(processed_data)

grouped length :10
  corrected_shirt_number              position  goals  total_shots  \
0                      7        Center Forward      0            0   
1                      8    Central Midfielder      0            0   
2                     14  Defensive Midfielder      0            0   
3                     28          Right Winger      0            0   
4                     46               Striker      0            0   
5                     70    Central Midfielder      0            0   
6                     11            Right-back      0            0   
7                     12  Attacking Midfielder      0            1   
8                     19            Goalkeeper      0            3   
9                     45           Left Winger      0            0   

   shots_on_target  shots_off_target  blocked_shots  saved_shots  \
0                0                 0              0            0   
1                0                 0              0            0   
2     